In [2]:
pip install scikit-learn geopandas -q

Note: you may need to restart the kernel to use updated packages.


In [3]:
import geopandas as gpd
from shapely.geometry import Point, Polygon
from sklearn.preprocessing import MinMaxScaler
import h3pandas
import numpy as np
import pandas as pd
import leafmap

In [4]:
schools = gpd.read_file("data/nyc/SchoolPoints_APS_2024_08_28 (1)/SchoolPoints_APS_2024_08_28.shp")
subways = gpd.read_file("data/nyc/nyc_subway_entrances/nyc_subway_entrances.shp")
bike_paths = gpd.read_file("data/nyc/New York City Bike Routes_20241223.geojson")
neighborhoods = gpd.read_file("https://raw.githubusercontent.com/HodgesWardElliott/custom-nyc-neighborhoods/refs/heads/master/custom-pedia-cities-nyc-Mar2018.geojson")
parks = gpd.read_file("data/nyc/Parks Properties_20241223.geojson")

In [5]:
schools = schools.to_crs("EPSG:3857")
subways = subways.to_crs("EPSG:3857")
bike_paths = bike_paths.to_crs("EPSG:3857")
neighborhoods = neighborhoods.to_crs("EPSG:3857")
parks = parks.to_crs("EPSG:3857")

# Analyze neighborhoods

In [6]:
# Analysis for each neighborhood
def analyze_neighborhood(neighborhood_geometry):
    # Count features intersecting the neighborhood boundary
    num_schools = schools[schools.geometry.intersects(neighborhood_geometry)].shape[0]
    num_subways = subways[subways.geometry.intersects(neighborhood_geometry)].shape[0]
    bike_path_length = bike_paths[bike_paths.geometry.intersects(neighborhood_geometry)].length.sum()
    park_area = parks[parks.geometry.intersects(neighborhood_geometry)].area.sum()

    return num_schools, num_subways, bike_path_length, park_area

In [7]:
# Apply analysis to each neighborhood
neighborhoods[['num_schools', 'num_subways', 'bike_path_length', 'park_area']] = neighborhoods.geometry.apply(
    lambda geom: pd.Series(analyze_neighborhood(geom))
)

In [8]:
neighborhoods.head(3)

neighborhood boroughCode        borough  \
0         Allerton           2          Bronx   
1  Alley Pond Park           4         Queens   
2    Arden Heights           5  Staten Island   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   
2  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-8220788.214 4993431.406, -8220479.3...         12.0   
1  POLYGON ((-8209070.244 4973902.938, -8209112.6...          0.0   
2  POLYGON ((-8256547.374 4947814.753, -8256546.8...          1.0   

   num_subways  bike_path_length     park_area  
0          5.0      12972.782695  5.191057e+05  
1          0.0       5886.886135  7.365924e+06  
2          0.0          0.000000  9.533262e+06

In [9]:
# Normalize results (0 to 1 scale)
scaler = MinMaxScaler()
columns_to_normalize = ['num_schools', 'num_subways', 'bike_path_length', 'park_area']
neighborhoods[columns_to_normalize] = scaler.fit_transform(neighborhoods[columns_to_normalize])

In [10]:
neighborhoods.head(3)

neighborhood boroughCode        borough  \
0         Allerton           2          Bronx   
1  Alley Pond Park           4         Queens   
2    Arden Heights           5  Staten Island   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   
2  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-8220788.214 4993431.406, -8220479.3...     0.193548   
1  POLYGON ((-8209070.244 4973902.938, -8209112.6...     0.000000   
2  POLYGON ((-8256547.374 4947814.753, -8256546.8...     0.016129   

   num_subways  bike_path_length  park_area  
0     0.045045          0.181510   0.026226  
1     0.000000          0.082367   0.372141  
2     0.000000          0.000000   0.481639

In [11]:
# Aggregate results using touching neighborhoods
def aggregate_touching_neighborhoods(neighborhood_index):
    current_geometry = neighborhoods.loc[neighborhood_index, 'geometry']
    touching_indices = neighborhoods[neighborhoods.geometry.touches(current_geometry)].index

    if not touching_indices.empty:
        neighbor_values = neighborhoods.loc[touching_indices, columns_to_normalize].mean()
    else:
        neighbor_values = neighborhoods.loc[neighborhood_index, columns_to_normalize]

    return neighbor_values

In [12]:
# Apply aggregation to each neighborhood
neighborhoods[columns_to_normalize] = neighborhoods.index.to_series().apply(
    lambda idx: aggregate_touching_neighborhoods(idx)
)


In [13]:
# Final normalization (0 to 1 scale)
neighborhoods[columns_to_normalize] = scaler.fit_transform(neighborhoods[columns_to_normalize])

In [14]:
neighborhoods.head(3)

neighborhood boroughCode        borough  \
0         Allerton           2          Bronx   
1  Alley Pond Park           4         Queens   
2    Arden Heights           5  Staten Island   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   
2  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-8220788.214 4993431.406, -8220479.3...     0.066667   
1  POLYGON ((-8209070.244 4973902.938, -8209112.6...     0.185185   
2  POLYGON ((-8256547.374 4947814.753, -8256546.8...     0.040741   

   num_subways  bike_path_length  park_area  
0     0.036585          0.009243   0.025121  
1     0.000000          0.203034   0.322221  
2     0.016260          0.079246   0.210843

In [15]:
neighborhoods['index_score'] = neighborhoods['num_schools'] + neighborhoods['num_subways'] + neighborhoods['bike_path_length'] + neighborhoods['park_area'] 

In [16]:
import leafmap

# Create a map object
m = leafmap.Map()

# Center the map on New York City (latitude, longitude) with a specific zoom level
m.set_center(-74.0060, 40.7128, zoom=12)

# Add data to the map
m.add_data(
    neighborhoods, column="index_score", scheme="Quantiles", cmap="Blues", legend_title="Index"
)

# Display the map
m


Map(center=[40.7128, -74.006], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zo…

In [17]:
# Save or visualize the results
neighborhoods.to_file("neighborhood_access_index.geojson", driver="GeoJSON")

# Set up the H3 Grid

In [18]:
neighborhoods = neighborhoods.to_crs('EPSG:4326')

In [19]:
resolution = 9  # Adjust resolution as needed
gdf_h3 = neighborhoods.h3.polyfill(resolution)

In [20]:
gdf_h3.head()

neighborhood boroughCode        borough  \
0         Allerton           2          Bronx   
1  Alley Pond Park           4         Queens   
2    Arden Heights           5  Staten Island   
3        Arlington           5  Staten Island   
4         Arrochar           5  Staten Island   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   
2  http://nyc.pediacities.com/Resource/Neighborho...   
3  http://nyc.pediacities.com/Resource/Neighborho...   
4  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
1  POLYGON ((-73.74333 40.73888, -73.74371 40.739...     0.185185   
2  POLYGON ((-74.16983 40.56108, -74.16982 40.561...     0.040741   
3  POLYGON ((-74.15975 40.64142, -74.15998 40.641...     0.000000   
4  POLYGON ((-74.06078 40.59319, -74.06079 40.593...     0.016667   

   num_subways  bike_path_length  park_area  index_score  category    color  \
0     0.036585          0.009243   0.025121     0.137616         1  #f7fbff   
1     0.000000          0.203034   0.322221     0.710440         4  #2171b5   
2     0.016260          0.079246   0.210843     0.347090         2  #c6dbef   
3     0.000000          0.000000   0.012868     0.012868         1  #f7fbff   
4     0.015244          0.080113   0.136984     0.249007         2  #c6dbef   

                                         h3_polyfill  
0  [892a1001387ffff, 892a1001033ffff, 892a100138b...  
1  [892a1005033ffff, 892a100546bffff, 892a10050d7...  
2  [892a106012fffff, 892a106016fffff, 892a1060eb3...  
3                                  [892a106267bffff]  
4  [892a1075343ffff, 892a1075353ffff, 892a10753ab...

In [21]:
gdf_h3 = neighborhoods.h3.polyfill(resolution, explode=True)
gdf_h3.head()

neighborhood boroughCode borough  \
0     Allerton           2   Bronx   
0     Allerton           2   Bronx   
0     Allerton           2   Bronx   
0     Allerton           2   Bronx   
0     Allerton           2   Bronx   

                                                X.id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
0  http://nyc.pediacities.com/Resource/Neighborho...   
0  http://nyc.pediacities.com/Resource/Neighborho...   
0  http://nyc.pediacities.com/Resource/Neighborho...   
0  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  num_schools  \
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   
0  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...     0.066667   

   num_subways  bike_path_length  park_area  index_score  category    color  \
0     0.036585          0.009243   0.025121     0.137616         1  #f7fbff   
0     0.036585          0.009243   0.025121     0.137616         1  #f7fbff   
0     0.036585          0.009243   0.025121     0.137616         1  #f7fbff   
0     0.036585          0.009243   0.025121     0.137616         1  #f7fbff   
0     0.036585          0.009243   0.025121     0.137616         1  #f7fbff   

       h3_polyfill  
0  892a1001387ffff  
0  892a1001033ffff  
0  892a100138bffff  
0  892a100106bffff  
0  892a100102fffff

In [22]:
# For all the rows that are not null, set the indez to its h3_polyfill index
gdf_h3 = gdf_h3[gdf_h3['h3_polyfill'].isnull() == False].set_index('h3_polyfill')
gdf_h3.index.name = None
gdf_h3

neighborhood boroughCode    borough  \
892a1001387ffff     Allerton           2      Bronx   
892a1001033ffff     Allerton           2      Bronx   
892a100138bffff     Allerton           2      Bronx   
892a100106bffff     Allerton           2      Bronx   
892a100102fffff     Allerton           2      Bronx   
...                      ...         ...        ...   
892a100ab6bffff       Harlem           1  Manhattan   
892a1008cbbffff       Harlem           1  Manhattan   
892a100ab5bffff       Harlem           1  Manhattan   
892a1008cb3ffff       Harlem           1  Manhattan   
892a100ab53ffff       Harlem           1  Manhattan   

                                                              X.id  \
892a1001387ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001033ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100138bffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100106bffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100102fffff  http://nyc.pediacities.com/Resource/Neighborho...   
...                                                            ...   
892a100ab6bffff                                               None   
892a1008cbbffff                                               None   
892a100ab5bffff                                               None   
892a1008cb3ffff                                               None   
892a100ab53ffff                                               None   

                                                          geometry  \
892a1001387ffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
892a1001033ffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
892a100138bffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
892a100106bffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
892a100102fffff  POLYGON ((-73.8486 40.87167, -73.84582 40.8702...   
...                                                            ...   
892a100ab6bffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   
892a1008cbbffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   
892a100ab5bffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   
892a1008cb3ffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   
892a100ab53ffff  POLYGON ((-73.93457 40.82815, -73.93442 40.827...   

                 num_schools  num_subways  bike_path_length  park_area  \
892a1001387ffff     0.066667     0.036585          0.009243   0.025121   
892a1001033ffff     0.066667     0.036585          0.009243   0.025121   
892a100138bffff     0.066667     0.036585          0.009243   0.025121   
892a100106bffff     0.066667     0.036585          0.009243   0.025121   
892a100102fffff     0.066667     0.036585          0.009243   0.025121   
...                      ...          ...               ...        ...   
892a100ab6bffff     0.507407     0.278455          0.584689   0.141232   
892a1008cbbffff     0.507407     0.278455          0.584689   0.141232   
892a100ab5bffff     0.507407     0.278455          0.584689   0.141232   
892a1008cb3ffff     0.507407     0.278455          0.584689   0.141232   
892a100ab53ffff     0.507407     0.278455          0.584689   0.141232   

                 index_score  category    color  
892a1001387ffff     0.137616         1  #f7fbff  
892a1001033ffff     0.137616         1  #f7fbff  
892a100138bffff     0.137616         1  #f7fbff  
892a100106bffff     0.137616         1  #f7fbff  
892a100102fffff     0.137616         1  #f7fbff  
...                      ...       ...      ...  
892a100ab6bffff     1.511784         5  #08306b  
892a1008cbbffff     1.511784         5  #08306b  
892a100ab5bffff     1.511784         5  #08306b  
892a1008cb3ffff     1.511784         5  #08306b  
892a100ab53ffff     1.511784         5  #08306b  

[7465 rows x 12 columns]

In [23]:
# Turn the h3 indexes to actual boundaries
gdf_h3 = gdf_h3.h3.h3_to_geo_boundary()

In [24]:
pip install folium matplotlib mapclassify -q

Note: you may need to restart the kernel to use updated packages.


In [25]:
gdf_h3.explore()

In [26]:
gdf_h3_proj = gdf_h3.to_crs('EPSG:3857')

In [27]:
# Analysis for each hex cell
def analyze_access(hex_geometry):
    # Buffer hex geometry
    buffer_1600m = hex_geometry.buffer(1600)
    buffer_800m = hex_geometry.buffer(800)

    # Count features within buffers
    num_schools = schools[schools.geometry.intersects(buffer_1600m)].shape[0]
    num_subways = subways[subways.geometry.intersects(buffer_1600m)].shape[0]
    bike_path_length = bike_paths[bike_paths.geometry.intersects(buffer_1600m)].length.sum()
    park_area = parks[parks.geometry.intersects(buffer_800m)].area.sum()

    return num_schools, num_subways, bike_path_length, park_area

In [28]:
gdf_h3_proj = gdf_h3.to_crs('EPSG:3857')

In [29]:
gdf_h3_proj[['num_schools', 'num_subways', 'bike_path_length', 'park_area']] = gdf_h3_proj.geometry.apply(
    lambda hex_geom: pd.Series(analyze_access(hex_geom))
)


In [30]:
gdf_h3_proj.head()

neighborhood boroughCode borough  \
892a1001387ffff     Allerton           2   Bronx   
892a1001033ffff     Allerton           2   Bronx   
892a100138bffff     Allerton           2   Bronx   
892a100106bffff     Allerton           2   Bronx   
892a100102fffff     Allerton           2   Bronx   

                                                              X.id  \
892a1001387ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001033ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100138bffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100106bffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100102fffff  http://nyc.pediacities.com/Resource/Neighborho...   

                                                          geometry  \
892a1001387ffff  POLYGON ((-8222210.323 4991831.096, -8222445.2...   
892a1001033ffff  POLYGON ((-8221298.977 4993421.02, -8221534.00...   
892a100138bffff  POLYGON ((-8222936.79 4992195.854, -8223171.74...   
892a100106bffff  POLYGON ((-8223207.83 4993355.679, -8223442.82...   
892a100102fffff  POLYGON ((-8221754.701 4992626.011, -8221989.6...   

                 num_schools  num_subways  bike_path_length     park_area  \
892a1001387ffff         19.0         12.0      24959.402316  5.093397e+06   
892a1001033ffff         23.0          7.0      34254.417830  1.911750e+04   
892a100138bffff         22.0         13.0      28437.849001  5.105859e+06   
892a100106bffff         28.0         12.0      32755.030721  5.656904e+06   
892a100102fffff         20.0         12.0      32762.831164  5.066436e+05   

                 index_score  category    color  
892a1001387ffff     0.137616         1  #f7fbff  
892a1001033ffff     0.137616         1  #f7fbff  
892a100138bffff     0.137616         1  #f7fbff  
892a100106bffff     0.137616         1  #f7fbff  
892a100102fffff     0.137616         1  #f7fbff

In [31]:
gdf_h3_proj['h3_index'] = gdf_h3_proj.index

# Run the normalization analysis

In [32]:
import h3

In [33]:
# Normalize results
scaler = MinMaxScaler()
normalized_columns = ['num_schools', 'num_subways', 'bike_path_length', 'park_area']
gdf_h3_proj[normalized_columns] = scaler.fit_transform(gdf_h3_proj[normalized_columns])

# Aggregate results using neighboring cells
def aggregate_neighbors(h3_index):
    neighbors = h3.k_ring(h3_index, 2)  # 2-k ring
    neighbor_values = gdf_h3_proj[gdf_h3_proj['h3_index'].isin(neighbors)][normalized_columns].mean()
    return neighbor_values

gdf_h3_proj[normalized_columns] = gdf_h3_proj['h3_index'].apply(
    lambda h3_index: aggregate_neighbors(h3_index)
)

# # Final normalized analysis
gdf_h3_proj[normalized_columns] = scaler.fit_transform(gdf_h3_proj[normalized_columns])

# Save or visualize the results
gdf_h3_proj.to_file("access_index.geojson", driver="GeoJSON")

In [34]:
gdf_h3_proj.head(3)

neighborhood boroughCode borough  \
892a1001387ffff     Allerton           2   Bronx   
892a1001033ffff     Allerton           2   Bronx   
892a100138bffff     Allerton           2   Bronx   

                                                              X.id  \
892a1001387ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a1001033ffff  http://nyc.pediacities.com/Resource/Neighborho...   
892a100138bffff  http://nyc.pediacities.com/Resource/Neighborho...   

                                                          geometry  \
892a1001387ffff  POLYGON ((-8222210.323 4991831.096, -8222445.2...   
892a1001033ffff  POLYGON ((-8221298.977 4993421.02, -8221534.00...   
892a100138bffff  POLYGON ((-8222936.79 4992195.854, -8223171.74...   

                 num_schools  num_subways  bike_path_length  park_area  \
892a1001387ffff     0.225973     0.057446          0.246058   0.157024   
892a1001033ffff     0.205378     0.033488          0.318515   0.020589   
892a100138bffff     0.252288     0.062619          0.249444   0.246401   

                 index_score  category    color         h3_index  
892a1001387ffff     0.137616         1  #f7fbff  892a1001387ffff  
892a1001033ffff     0.137616         1  #f7fbff  892a1001033ffff  
892a100138bffff     0.137616         1  #f7fbff  892a100138bffff

# Create the total score

In [35]:
gdf_h3_proj['index_score'] = gdf_h3_proj['num_schools'] + gdf_h3_proj['num_subways'] + gdf_h3_proj['bike_path_length'] + gdf_h3_proj['park_area'] 

In [36]:
import leafmap

In [37]:
gdf_h3_map = gdf_h3_proj.to_crs('EPSG:4326')

In [40]:
m = leafmap.Map()
m.add_data(
    gdf_h3_map, column="index_score", scheme="Quantiles", cmap="Blues", legend_title="Index"
)
m

Map(center=[20, 0], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_text…

From the map one can see the status of various cells with those with a darker shade of blue having a better score.